In [ ]:
# There are two standard ways to do linear programming in python:
# cvxopt and scipy.
# We use scipy, which has a cleaner API, even though it's usually a bit slower.

# pip install scipy
import scipy.optimize
# https://docs.scipy.org/doc/scipy/reference/optimize.html

import numpy as np

Problem 1: a balanced diet
-------------------

Given the nutrition information and cost of a bunch of foods, and your nutrition requirements, find the cheapest collection of food to eat.

In [ ]:
import csv
import io

def parse_csv(s):
    """Utility function to parse a CSV into a list of dictionaries.
    
    Parses numeric quantities as floats if possible.
    """
    generator = csv.DictReader(io.StringIO(s), skipinitialspace=True)
    answer = list(generator)
    for d in answer:
        for k in d:
            try:
                d[k] = float(d[k])
            except ValueError:
                pass
    return answer

# A random selection of foods you are interested in eating
foods = parse_csv("""
name,            calories, fat, carbs, protein,  cost, sodium
doritos (bag),        150,   8,    17,       2,  0.99,    180
soylent (bottle),     400,  21,    36,      20,  3.25,    300
bok choy (cup),       100, 1.5,    15,    13.5,  1.85,     58
hummus (cup),         409,  24,    35,      19,  2.22,    932
pizza (slice),        304,  11,    38,      13,  2.00,    640
chicken (1/2 lb),     372,   8,     0,      70,  1.60,    165
""".strip())


# Dietary recommendations vary by gender/age/weight/activity level.
#  https://www.nal.usda.gov/fnic/dri-calculator/
# This is for a 20-year-old sedentary 150-lb 5'9" man.

nutrients = parse_csv("""
name,      min,   max
calories, 2400,  2600
fat,        56,    97
carbs,     281,   406
protein,    55,   999
sodium,   1500,  2300
""".strip())

# Fun fact: I initially didn't include sodium as a nutrient.  The recommended diet was almost entirely pizza.

In [ ]:
# This is the format:
print(foods[0])
print(nutrients)

In [ ]:
# Let's find the cheapest collection of food that satisfies our nutrition requirements

def solve(foods, nutrients):
    """Given the collection of foods and nutrient requirements, find the cheapest possible diet.
    
    Here a "diet" is the amount of each food eaten.
    """
    
    # First, produce the linear program.
    
    # One variable per food
    # two constraints per nutrient
    A = []
    b = []
    for nutrient in nutrients:
        name = nutrient['name']  # (e.g., "fat")
        # Get the list of this nutrient in each food item
        row = np.array([food[name] for food in foods])

        # Then row dot diet is our total consumption of this nutrient.
        # It should lie between nutrient[min] and nutrient[max].
        
        A.append(-row)                # Lower bound
        b.append(-nutrient['min'])

        A.append(row)                 # Upper bound
        b.append(nutrient['max'])


    # c dot diet gives the total cost of our diet
    c = [food['cost'] for food in foods]
    A, b, c = map(np.array, (A, b, c))

    
    # Now, optimize it.

    result = scipy.optimize.linprog(c, A, b)

    print(result)
    print()

    
    print('Components of a "balanced" diet:')
    for food, val in zip(foods, result['x']):
        print(f"{food['name'].rjust(20)}    {val:0.2f}")

    print()
    print('Resulting nutrition:')
    nutrition = A[1::2].dot(result['x'])   # Every odd row is the +row
    for nutrient, val in zip(nutrients, nutrition):
        print(f"{nutrient['name'].rjust(20)}    {val:0.2f}")
    print()
    print("Cost of diet:", c.dot(result['x']))
              
    # Problem 1.a : compute dual variables here.

              
solve(foods, nutrients)
# Note: nutrition is complicated. Actually following this diet is not recommended.

Problem 1.a
-----------------

Consider the dual linear program.  How many variables are there?  What do they represent?  Can you predict which dual variables will be zero?

Now modify the above linear program to also compute and output the dual variables.  Hint: computing the result is one line of code: just call `scipy.optimize.linprog` after reordering, transposing, and/or flipping the signs of the variables `A, b, c`.  The objective value should be the same (but maybe with a different sign).  You'll then want a few more lines to output the dual variables in a clear format.

What are the largest dual variables in your solution, and what do they represent?

Problem 1.b
-----------------
Suppose that you believe the story here:

https://www.npr.org/sections/thetwo-way/2016/09/13/493739074/50-years-ago-sugar-industry-quietly-paid-scientists-to-point-blame-at-fat
http://time.com/4130043/lobbying-politics-dietary-guidelines/

that the sugar lobby has gotten the government to require too much carbs, and be too restrictive on fat.  Is that consistent with your observations in part (b)?


How much would the cost of the diet change if you allowed yourself 5g more fat per day?  How about 5g less carbs per day?

First, try to make a prediction using your dual variables.  Then compute the actual value, as below.  If you didn't predict it correctly beforehand, figure out how you should have predicted it.

Would the same prediction method work if you allowed 1000g more fat per day?  If not, why not?

In [ ]:
new_nutrients = XXX

solve(foods, new_nutrients)

Problem 1.c
-----------------

Now compute _your_ "optimally tasty" diet.  Find the nutrition information of foods you eat, and choose daily nutrition goals for yourself.  Give yourself a daily budget, and assign a "tastiness" to each food.

What is the maximally tasty selection of food that fits into your budget and satisfies your nutritional requirements?